In [25]:
import pickle, gzip
import numpy as np
from numpy.core.fromnumeric import argmax, reshape
from numpy.lib.twodim_base import mask_indices
import copy
from scipy.ndimage.interpolation import shift

with gzip.open('mnist.pkl.gz', 'rb') as fd:
    (train_set, label_set),  (valid_set,valid_label_set), (test_set, test_label_set) = pickle.load(fd, encoding = 'latin')

first_layer = []
first_biases = []
last_layer = []
last_biases = []


def weight_initialization():
    # initialize weights with mean = 0 and st.dev.= 1/sqrt(nr of neurons)
    global first_layer, first_biases, last_layer, last_biases
    first_layer = np.random.normal(0,np.sqrt(1/784), (100,784))
    first_biases = np.random.normal(0, 1, 100)

    last_layer = np.random.normal(0,np.sqrt(1/100), (10,100))
    last_biases = np.random.normal(0, 1, 10)


def softmax(x):
    x_aux = np.exp(x)
    #print(np.sum(x_aux))
    return x_aux / np.sum(x_aux)

def sigmoid(x):
    return np.divide(np.exp(x), np.exp(x) + 1)

def dropout(layer, drop_probability):
    hidden_neurons = int(drop_probability * 100)
    mask = np.full(hidden_neurons, 0)
    mask = np.append(mask,np.full(100 - hidden_neurons, 1))
    np.random.shuffle(mask)
    mask_inverse = mask ^ 1
    #print(layer.shape,"-",mask.shape,"-",np.sum(mask))
    #print(mask_inverse.shape, mask.shape)
    return (layer * mask, layer * mask_inverse, mask)

# def shift_image(image, dx, dy):
#     image = image.reshape((28, 28))
#     shifted_image = shift(image, [dy, dx], cval=0, mode="constant")
#     return shifted_image.reshape([-1])

# def data_augumentation():
#     #https://towardsdatascience.com/improving-accuracy-on-mnist-using-data-augmentation-b5c38eb5a903
#     global train_set, label_set
#     augmented_images = copy.deepcopy(train_set)
#     augmented_labels = copy.deepcopy(label_set)
#     ct = 0
#     for dx, dy in ((1, 0), (-1, 0), (0, 1), (0, -1)):
#         for (image, label) in zip(train_set, label_set):
#             augmented_images = np.append(augmented_images, shift_image(image, dx, dy))
#             augmented_labels = np.append(augmented_labels, label)
#             ct += 1
#             if ct == 10000:
#                 break
#         if ct == 10000:
#                 break
#     train_set = augmented_images.reshape((-1, 784))
#     label_set = augmented_labels

def data_augumentation():
    global train_set, label_set, valid_set, valid_label_set
    train_set = np.append(train_set,[valid_set]).reshape((-1, 784))
    label_set = np.append(label_set,valid_label_set)


def training_alg(nrIterations):
    learning_rate = 0.05
    global first_layer, first_biases, last_layer, last_biases
    data_augumentation()
    while  nrIterations > 0:
        for k in range(len(train_set)):
           # get the output value for all perceptrons at once on each layer
            first_layer_output = sigmoid(np.sum((np.dot(first_layer, train_set[k]),first_biases),axis = 0))
            #100,784 x 784,1 = 100,1
            (last_layer, last_layer_dropped, mask) = dropout(last_layer,0.3) 
            #print(last_layer_modified.shape)
            last_layer_output = softmax(np.sum((np.dot(last_layer, first_layer_output),last_biases), axis = 0))
            # 10, 100 x 100,1 = 10,1

            label_value = np.zeros(10)
            label_value[label_set[k]] = 1
            #backprop & cross entropy # slide 14-15
            last_cost = (last_layer_output - label_value) # (10,)
            
            first_cost = first_layer_output * (1 - first_layer_output)

            first_cost = (first_cost * np.sum((last_layer * last_cost.reshape((10,1))), axis = 0))

            #update
            last_layer = last_layer - last_cost.reshape((10,1)) * first_layer_output * learning_rate
            first_layer = first_layer - first_cost.reshape((100,1)) * train_set[k] * learning_rate

            last_biases  = last_biases - last_cost * learning_rate
            first_biases = first_biases - first_cost * learning_rate
       
            # restoring the hidden neurons
            last_layer = last_layer * mask
            last_layer = np.sum((last_layer, last_layer_dropped), axis=0) 
        nrIterations -=1
        test_alg()
    return (first_layer, first_cost, last_layer, last_cost)   


def test_alg():
    corectly_classified = 0
    for k in range(len(test_set)):
        first_layer_output = sigmoid(np.sum((np.dot(first_layer, test_set[k]),first_biases),axis = 0)) 
        last_layer_output = softmax(np.sum((np.dot(last_layer, first_layer_output),last_biases), axis = 0))
        perceptr = np.argmax(last_layer_output)
        if test_label_set[k] == perceptr:
            corectly_classified += 1
    print(corectly_classified, len(test_set))
    print("acuraccy = ", float( corectly_classified / len(test_set)) * 100)  

if __name__ == '__main__':
    weight_initialization()
    first_layer, first_cost, last_layer, last_cost = training_alg(1)


(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(

(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)

(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)

(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)

(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(

...

(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(

(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)

(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)

(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)
(100,)
end
(100,)
(10,)
(100,)
(10,)
(100,)

KeyboardInterrupt: 